In [1]:
!pip install -q h2o

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 265.9/265.9 MB 5.1 MB/s eta 0:00:00


In [2]:
import pandas as pd
import numpy as np
from sklearn.metrics import mean_absolute_error, mean_absolute_percentage_error
import os
import pickle

import h2o
from h2o.automl import H2OAutoML

In [3]:
import warnings
warnings.filterwarnings('ignore')

In [4]:
path = '/content/drive/MyDrive/datasets/Multimodal_EarningCallTranscripts_Analysis_India/'

In [5]:
# Start the H2O cluster (locally)
h2o.init()

Checking whether there is an H2O instance running at http://localhost:54321..... not found.
Attempting to start a local H2O server...
  Java Version: openjdk version "11.0.26" 2025-01-21; OpenJDK Runtime Environment (build 11.0.26+4-post-Ubuntu-1ubuntu122.04); OpenJDK 64-Bit Server VM (build 11.0.26+4-post-Ubuntu-1ubuntu122.04, mixed mode, sharing)
  Starting server from /usr/local/lib/python3.11/dist-packages/h2o/backend/bin/h2o.jar
  Ice root: /tmp/tmpr3sbymez
  JVM stdout: /tmp/tmpr3sbymez/h2o_unknownUser_started_from_python.out
  JVM stderr: /tmp/tmpr3sbymez/h2o_unknownUser_started_from_python.err
  Server is running at http://127.0.0.1:54321
Connecting to H2O server at http://127.0.0.1:54321 ... successful.


--------------------------  -----------------------------------------------------------------------------------------
H2O_cluster_uptime:         08 secs
H2O_cluster_timezone:       Etc/UTC
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.46.0.7
H2O_cluster_version_age:    12 days
H2O_cluster_name:           H2O_from_python_unknownUser_wkm3dv
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    3.170 Gb
H2O_cluster_total_cores:    2
H2O_cluster_allowed_cores:  2
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://127.0.0.1:54321
H2O_connection_proxy:       {"http": null, "https": null, "colab_language_server": "/usr/colab/bin/language_service"}
H2O_internal_security:      False
Python_version:             3.11.11 final
--------------------------  -----------------------------------------------------------------------------------------

# Data Loading

In [6]:
final_with_funda = pd.read_excel(path+'MiMIC_Multi-Modal_Indian_Earnings_Calls.xlsx')
final_with_funda.head()

company_name         ticker          company_website_link  \
0               L&T Finance Ltd        NSE:LTF          http://www.ltfs.com/   
1               L&T Finance Ltd        NSE:LTF          http://www.ltfs.com/   
2  Max Healthcare Institute Ltd  NSE:MAXHEALTH  http://www.maxhealthcare.in/   
3  Max Healthcare Institute Ltd  NSE:MAXHEALTH  http://www.maxhealthcare.in/   
4  Max Healthcare Institute Ltd  NSE:MAXHEALTH  http://www.maxhealthcare.in/   

                                       screener_link  \
0  https://www.screener.in/company/LTF/consolidated/   
1  https://www.screener.in/company/LTF/consolidated/   
2  https://www.screener.in/company/MAXHEALTH/cons...   
3  https://www.screener.in/company/MAXHEALTH/cons...   
4  https://www.screener.in/company/MAXHEALTH/cons...   

                                     transcript_link  \
0                                                NaN   
1  https://www.bseindia.com/stockinfo/AnnPdfOpen....   
2  https://www.bseindia.com/stockinfo/AnnPdfOpen....   
3  https://www.bseindia.com/stockinfo/AnnPdfOpen....   
4                                                NaN   

                transcript_file_name  \
0                      NOT AVAILABLE   
1        LTF_Jul-2024_transcript.pdf   
2  MAXHEALTH_Nov-2024_transcript.pdf   
3  MAXHEALTH_Aug-2024_transcript.pdf   
4                      NOT AVAILABLE   

                                            ppt_link  \
0  https://www.bseindia.com/stockinfo/AnnPdfOpen....   
1  https://www.bseindia.com/stockinfo/AnnPdfOpen....   
2  https://www.bseindia.com/stockinfo/AnnPdfOpen....   
3  https://www.bseindia.com/xml-data/corpfiling/A...   
4  https://www.bseindia.com/stockinfo/AnnPdfOpen....   

                ppt_file_name         RESULT DATE  year  ...  \
0        LTF_Oct-2024_ppt.pdf 2024-10-18 15:30:00  2024  ...   
1               NOT AVAILABLE 2024-07-16 15:30:00  2024  ...   
2  MAXHEALTH_Nov-2024_ppt.pdf 2024-11-05 15:30:00  2024  ...   
3  MAXHEALTH_Aug-2024_ppt.pdf 2024-08-01 15:30:00  2024  ...   
4  MAXHEALTH_Jan-2024_ppt.pdf 2024-01-31 15:30:00  2024  ...   

   Cash from Financing Activity  Net Cash Flow Revenue  Financing Profit  \
0                       -7037.0        -5515.0     NaN               NaN   
1                       -7037.0        -5515.0     NaN               NaN   
2                        -264.0         -394.0     NaN               NaN   
3                        -264.0         -394.0     NaN               NaN   
4                        -264.0         -394.0     NaN               NaN   

   Financing Margin %  Deposits  Borrowing  RESULT DATE+1 open price  \
0                 NaN       NaN        NaN                     168.0   
1                 NaN       NaN        NaN                     189.9   
2                 NaN       NaN        NaN                    1043.0   
3                 NaN       NaN        NaN                     920.0   
4                 NaN       NaN        NaN                     780.0   

   TARGET-2 REGRESSION NORMALIZED       split  
0                        0.012048        test  
1                        0.018504  validation  
2                        0.012621        test  
3                       -0.015990  validation  
4                        0.062598       train  

[5 rows x 57 columns]

In [ ]:
final_with_funda.shape

(1042, 57)

In [ ]:
final_with_funda.columns

Index(['company_name', 'ticker', 'company_website_link', 'screener_link',
       'transcript_link', 'transcript_file_name', 'ppt_link', 'ppt_file_name',
       'RESULT DATE', 'year', 'month_numeric', 'RESULT DATE open price',
       'RESULT DATE+1', 'SMA20', 'SMA50', 'RSI14', 'gdp_growth', 'inflation',
       'NIFTY50_open', 'NIFTY50_close', 'NIFTY50_volume', 'previous_year',
       'financial_year', 'Sales', 'Expenses', 'Operating Profit', 'OPM %',
       'Other Income', 'Interest', 'Depreciation', 'Profit before tax',
       'Tax %', 'Net Profit', 'EPS in Rs', 'Dividend Payout %',
       'Equity Capital', 'Reserves', 'Borrowings', 'Other Liabilities',
       'Total Liabilities', 'Fixed Assets', 'CWIP', 'Investments',
       'Other Assets', 'Total Assets', 'Cash from Operating Activity',
       'Cash from Investing Activity', 'Cash from Financing Activity',
       'Net Cash Flow', 'Revenue', 'Financing Profit', 'Financing Margin %',
       'Deposits', 'Borrowing', 'RESULT DATE+1 open 

In [7]:
def convert_str_to_txt(x):
  try:
    return float(x.replace('%', '').replace(',',''))
  except:
    return x

for col in ['OPM %', 'Tax %', 'Dividend Payout %', 'Financing Margin %']:
  final_with_funda[col] = final_with_funda[col].apply( lambda x : convert_str_to_txt(x))

In [19]:
final_with_funda['classification'] = final_with_funda['TARGET-2 REGRESSION NORMALIZED'].apply(lambda x : 1 if x > 0 else 0)

In [8]:
def calculate_regression_metrics(y_true, y_pred):
    """
    Calculates MAE, RMSE for regression tasks.

    Args:
        y_true: A list or array of true values.
        y_pred: A list or array of predicted values.

    Returns:
        A dictionary containing the calculated metrics.
    """
    metrics = {}

    # Convert lists to numpy arrays
    y_true = np.array(y_true)
    y_pred = np.array(y_pred)

    # Mean Absolute Error (MAE)
    metrics['MAE'] = mean_absolute_error(y_true, y_pred)

    # Root Mean Squared Error (RMSE)
    metrics['RMSE'] = np.sqrt(np.mean((y_true - y_pred)**2))

    metrics['MAPE'] = mean_absolute_percentage_error(y_true, y_pred)

    return metrics

# Using Numeric Data Only

In [ ]:
train = final_with_funda[final_with_funda['split'] == 'train']
valid = final_with_funda[final_with_funda['split'] == 'validation']
test = final_with_funda[final_with_funda['split'] == 'test']
print(train.shape, valid.shape, test.shape)

(832, 57) (103, 57) (107, 57)


In [ ]:
x_cols_to_use = ['RESULT DATE open price', 'SMA20', 'SMA50', 'RSI14',
                 'gdp_growth', 'inflation', 'NIFTY50_open', 'NIFTY50_close', 'NIFTY50_volume',
                 'Sales', 'Expenses', 'Operating Profit', 'OPM %', 'Other Income', 'Interest',
                 'Depreciation', 'Profit before tax', 'Tax %', 'Net Profit',
                 'EPS in Rs', 'Dividend Payout %', 'Equity Capital', 'Reserves',
                 'Borrowings', 'Other Liabilities', 'Total Liabilities',
                 'Fixed Assets', 'CWIP', 'Investments', 'Other Assets',
                 'Total Assets', 'Cash from Operating Activity',
                 'Cash from Investing Activity', 'Cash from Financing Activity',
                 'Net Cash Flow', 'Revenue', 'Financing Profit', 'Financing Margin %',
                 'Deposits', 'Borrowing']


y_col =  'RESULT DATE+1 open price'#'TARGET-2 REGRESSION NORMALIZED'

h2o_train = h2o.H2OFrame(train[x_cols_to_use])  # Convert train DataFrame to H2OFrame
h2o_valid = h2o.H2OFrame(valid[x_cols_to_use])  # Convert valid DataFrame to H2OFrame
h2o_test = h2o.H2OFrame(test[x_cols_to_use])  # Convert test DataFrame to H2OFrame

h2o_train[y_col] = h2o.H2OFrame(train[y_col].to_list())  # Convert Pandas Series to H2OFrame before assigning
h2o_valid[y_col] = h2o.H2OFrame(valid[y_col].to_list())  # Convert Pandas Series to H2OFrame before assigning
h2o_test[y_col] = h2o.H2OFrame(test[y_col].to_list())  # Convert Pandas Series to H2OFrame before assigning

aml = H2OAutoML(max_models=20, seed=1,nfolds = 0)
aml.train(x=x_cols_to_use, y=y_col, training_frame=h2o_train,validation_frame=h2o_valid)

# View the AutoML Leaderboard
lb = aml.leaderboard
lb.head(rows=lb.nrows)

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
AutoML progress: |███████████████████████████████████████████████████████████████| (done) 100%


model_id                                                  rmse               mse       mae      rmsle    mean_residual_deviance
----------------------------------------------------  --------  ----------------  --------  ---------  ------------------------
DeepLearning_grid_1_AutoML_1_20250409_125927_model_1   124.274   15444              92.95   0.186283            15444
DeepLearning_grid_2_AutoML_1_20250409_125927_model_1   148.476   22045.2           102.05   0.263675            22045.2
DeepLearning_grid_3_AutoML_1_20250409_125927_model_1   232.249   53939.5           138.35   0.21911             53939.5
GBM_5_AutoML_1_20250409_125927                         347.979  121089             116.301  0.055101           121089
XGBoost_3_AutoML_1_20250409_125927                     360.731  130127             142.876  0.12462            130127
XGBoost_grid_1_AutoML_1_20250409_125927_model_2        360.877  130232             132.802  0.0704741          130232
XGBoost_grid_1_AutoML_1_20250409_125927_model_3        362.277  131245             114.346  0.0618231          131245
GBM_grid_1_AutoML_1_20250409_125927_model_2            363.447  132094             115.479  0.0740894          132094
XGBoost_2_AutoML_1_20250409_125927                     373.977  139859             133.238  0.0886959          139859
GBM_3_AutoML_1_20250409_125927                         386.865  149664             115.389  0.0703277          149664
XGBoost_1_AutoML_1_20250409_125927                     389.489  151702             143.901  0.0940194          151702
GBM_2_AutoML_1_20250409_125927                         390.618  152582             116.687  0.0778867          152582
GBM_4_AutoML_1_20250409_125927                         406.879  165550             118.116  0.0858482          165550
DeepLearning_1_AutoML_1_20250409_125927                410.255  168309             226.432  0.447204           168309
XRT_1_AutoML_1_20250409_125927                         426.22   181663             153.543  0.0815366          181663
DRF_1_AutoML_1_20250409_125927                         426.821  182176             140.027  0.0642774          182176
XGBoost_grid_1_AutoML_1_20250409_125927_model_1        428.699  183783             179.014  0.115927           183783
GBM_grid_1_AutoML_1_20250409_125927_model_1            476.34   226900             211.895  0.227544           226900
GBM_1_AutoML_1_20250409_125927                        1160.2         1.34606e+06   465.625  0.278133                1.34606e+06
GLM_1_AutoML_1_20250409_125927                        2474.66        6.12395e+06  1514.8    1.18928                 6.12395e+06
[20 rows x 6 columns]

In [ ]:
lb = h2o.automl.get_leaderboard(aml, extra_columns = "ALL")
lb

model_id                                                 rmse       mse      mae      rmsle    mean_residual_deviance    training_time_ms    predict_time_per_row_ms  algo
----------------------------------------------------  -------  --------  -------  ---------  ------------------------  ------------------  -------------------------  ------------
DeepLearning_grid_1_AutoML_1_20250409_125927_model_1  124.274   15444     92.95   0.186283                    15444                 90000                   0.130107  DeepLearning
DeepLearning_grid_2_AutoML_1_20250409_125927_model_1  148.476   22045.2  102.05   0.263675                    22045.2               66419                   0.209791  DeepLearning
DeepLearning_grid_3_AutoML_1_20250409_125927_model_1  232.249   53939.5  138.35   0.21911                     53939.5               51729                   0.152972  DeepLearning
GBM_5_AutoML_1_20250409_125927                        347.979  121089    116.301  0.055101                   121089                  3756                   0.215801  GBM
XGBoost_3_AutoML_1_20250409_125927                    360.731  130127    142.876  0.12462                    130127                  1275                   0.303849  XGBoost
XGBoost_grid_1_AutoML_1_20250409_125927_model_2       360.877  130232    132.802  0.0704741                  130232                  5185                   0.236808  XGBoost
XGBoost_grid_1_AutoML_1_20250409_125927_model_3       362.277  131245    114.346  0.0618231                  131245                  7255                   0.100218  XGBoost
GBM_grid_1_AutoML_1_20250409_125927_model_2           363.447  132094    115.479  0.0740894                  132094                  1154                   0.086248  GBM
XGBoost_2_AutoML_1_20250409_125927                    373.977  139859    133.238  0.0886959                  139859                  4713                   0.110586  XGBoost
GBM_3_AutoML_1_20250409_125927                        386.865  149664    115.389  0.0703277                  149664                  4115                   0.17295   GBM
[20 rows x 9 columns]

In [ ]:
# Get the best model using the metric
m = aml.leader
print(m)

Model Details
H2ODeepLearningEstimator : Deep Learning
Model Key: DeepLearning_grid_1_AutoML_1_20250409_125927_model_1


Status of Neuron Layers: predicting RESULT DATE+1 open price, regression, gaussian distribution, Quadratic loss, 28,101 weights/biases, 345.4 KB, 509,954 training samples, mini-batch size 1
    layer    units    type              dropout    l1    l2    mean_rate              rate_rms               momentum    mean_weight             weight_rms           mean_bias             bias_rms
--  -------  -------  ----------------  ---------  ----  ----  ---------------------  ---------------------  ----------  ----------------------  -------------------  --------------------  -----------------------
    1        279      Input             15.0
    2        100      RectifierDropout  10.0       0.0   0.0   0.0469522964567144     0.1403437852859497     0.0         -0.0034428720702365887  0.0753689706325531   0.11255552116543806   0.12360426783561707
    3        1        Linea

In [ ]:
# this is equivalent to
m = aml.get_best_model()
print(m)

Model Details
H2ODeepLearningEstimator : Deep Learning
Model Key: DeepLearning_grid_1_AutoML_1_20250409_125927_model_1


Status of Neuron Layers: predicting RESULT DATE+1 open price, regression, gaussian distribution, Quadratic loss, 28,101 weights/biases, 345.4 KB, 509,954 training samples, mini-batch size 1
    layer    units    type              dropout    l1    l2    mean_rate              rate_rms               momentum    mean_weight             weight_rms           mean_bias             bias_rms
--  -------  -------  ----------------  ---------  ----  ----  ---------------------  ---------------------  ----------  ----------------------  -------------------  --------------------  -----------------------
    1        279      Input             15.0
    2        100      RectifierDropout  10.0       0.0   0.0   0.0469522964567144     0.1403437852859497     0.0         -0.0034428720702365887  0.0753689706325531   0.11255552116543806   0.12360426783561707
    3        1        Linea

In [ ]:
# Get the best model using a non-default metric
m = aml.get_best_model(criterion="RMSE")
print(m)

Model Details
H2ODeepLearningEstimator : Deep Learning
Model Key: DeepLearning_grid_1_AutoML_1_20250409_125927_model_1


Status of Neuron Layers: predicting RESULT DATE+1 open price, regression, gaussian distribution, Quadratic loss, 28,101 weights/biases, 345.4 KB, 509,954 training samples, mini-batch size 1
    layer    units    type              dropout    l1    l2    mean_rate              rate_rms               momentum    mean_weight             weight_rms           mean_bias             bias_rms
--  -------  -------  ----------------  ---------  ----  ----  ---------------------  ---------------------  ----------  ----------------------  -------------------  --------------------  -----------------------
    1        279      Input             15.0
    2        100      RectifierDropout  10.0       0.0   0.0   0.0469522964567144     0.1403437852859497     0.0         -0.0034428720702365887  0.0753689706325531   0.11255552116543806   0.12360426783561707
    3        1        Linea

In [ ]:
# Get training timing info
info = aml.training_info
print(info)

{'creation_epoch': '1744203567', 'start_epoch': '1744203567', 'start_XGBoost_def_2': '1744203567', 'start_GLM_def_1': '1744203574', 'start_GBM_def_5': '1744203575', 'start_XGBoost_def_1': '1744203579', 'start_DRF_def_1': '1744203584', 'start_GBM_def_2': '1744203588', 'start_GBM_def_3': '1744203593', 'start_GBM_def_4': '1744203598', 'start_XGBoost_def_3': '1744203600', 'start_DRF_XRT': '1744203602', 'start_GBM_def_1': '1744203606', 'start_DeepLearning_def_1': '1744203610', 'start_XGBoost_grid_1': '1744203612', 'start_GBM_grid_1': '1744203628', 'start_DeepLearning_grid_1': '1744203631', 'start_DeepLearning_grid_2': '1744203721', 'start_DeepLearning_grid_3': '1744203788', 'stop_epoch': '1744203840', 'duration_secs': '273'}


In [ ]:
aml.leader.model_id

'DeepLearning_grid_1_AutoML_1_20250409_125927_model_1'

In [ ]:
preds_leader = aml.leader.predict(h2o_test)
preds_leader

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%


predict
---------
  43.8964
 875.223
1938.47
 139.043
 186.102
3058.43
4610.1
 670.982
 649.744
1009.34
[107 rows x 1 column]

In [ ]:
print("\n TRAIN SET \n")
train_predictions = aml.leader.predict(h2o_train).as_data_frame()['predict'].to_list()
print(calculate_regression_metrics(train[y_col], train_predictions))


print("\n VALID SET \n")
valid_predictions = aml.leader.predict(h2o_valid).as_data_frame()['predict'].to_list()
print(calculate_regression_metrics(valid[y_col], valid_predictions))


print("\n TEST SET \n")
test_predictions = aml.leader.predict(h2o_test).as_data_frame()['predict'].to_list()
print(calculate_regression_metrics(test[y_col],test_predictions))


 TRAIN SET 

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%
{'MAE': 103.43077778665219, 'RMSE': np.float64(136.46244339115717), 'MAPE': 0.4104183904685377}

 VALID SET 

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%
{'MAE': 92.95005429027556, 'RMSE': np.float64(124.27373841117173), 'MAPE': 0.11078708574728854}

 TEST SET 

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%
{'MAE': 150.76924019481663, 'RMSE': np.float64(269.1930438865622), 'MAPE': 0.28824375358902776}


# Using Numeric and Text Data Classifier Probabilities

In [20]:
for col in final_with_funda.columns:
  if 'text_embeddings' in col:
    print(col)
    del final_with_funda[col]

all_embeddings_128 = pickle.load(open(path + 'getting_all_texts_together_embeddings_dim128_CPU.pkl', 'rb'))
final_with_funda['text_embeddings'] = all_embeddings_128

for i in range(128):
  final_with_funda['text_embeddings_' + str(i)] = final_with_funda['text_embeddings'].apply(lambda x : x[i])

text_features = ['text_embeddings_' + str(i) for i in range(128)]

train = final_with_funda[final_with_funda['split'] == 'train']
valid = final_with_funda[final_with_funda['split'] == 'validation']
test = final_with_funda[final_with_funda['split'] == 'test']

x_cols_to_use =  text_features

text_embeddings
text_embeddings_0
text_embeddings_1
text_embeddings_2
text_embeddings_3
text_embeddings_4
text_embeddings_5
text_embeddings_6
text_embeddings_7
text_embeddings_8
text_embeddings_9
text_embeddings_10
text_embeddings_11
text_embeddings_12
text_embeddings_13
text_embeddings_14
text_embeddings_15
text_embeddings_16
text_embeddings_17
text_embeddings_18
text_embeddings_19
text_embeddings_20
text_embeddings_21
text_embeddings_22
text_embeddings_23
text_embeddings_24
text_embeddings_25
text_embeddings_26
text_embeddings_27
text_embeddings_28
text_embeddings_29
text_embeddings_30
text_embeddings_31
text_embeddings_32
text_embeddings_33
text_embeddings_34
text_embeddings_35
text_embeddings_36
text_embeddings_37
text_embeddings_38
text_embeddings_39
text_embeddings_40
text_embeddings_41
text_embeddings_42
text_embeddings_43
text_embeddings_44
text_embeddings_45
text_embeddings_46
text_embeddings_47
text_embeddings_48
text_embeddings_49
text_embeddings_50
text_embeddings_51
text_e

In [21]:
y_col = 'classification' #'RESULT DATE+1 open price' #'TARGET-2 REGRESSION NORMALIZED'

h2o_train = h2o.H2OFrame(train[x_cols_to_use])  # Convert train DataFrame to H2OFrame
h2o_valid = h2o.H2OFrame(valid[x_cols_to_use])  # Convert valid DataFrame to H2OFrame
h2o_test = h2o.H2OFrame(test[x_cols_to_use])  # Convert test DataFrame to H2OFrame

h2o_train[y_col] = h2o.H2OFrame(train[y_col].to_list()).asfactor()  # Convert Pandas Series to H2OFrame before assigning
h2o_valid[y_col] = h2o.H2OFrame(valid[y_col].to_list()).asfactor()  # Convert Pandas Series to H2OFrame before assigning
h2o_test[y_col] = h2o.H2OFrame(test[y_col].to_list()).asfactor()  # Convert Pandas Series to H2OFrame before assigning

aml = H2OAutoML(max_models=20, seed=1,nfolds = 0)
aml.train(x=x_cols_to_use, y=y_col, training_frame=h2o_train,validation_frame=h2o_valid)

# View the AutoML Leaderboard
lb = aml.leaderboard
lb.head(rows=lb.nrows)

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
AutoML progress: |███████████████████████████████████████████████████████████████| (done) 100%


model_id                                                   auc    logloss     aucpr    mean_per_class_error      rmse       mse
----------------------------------------------------  --------  ---------  --------  ----------------------  --------  --------
XGBoost_2_AutoML_2_20250409_152135                    0.521682   0.868195  0.519441                0.490196  0.55289   0.305688
DRF_1_AutoML_2_20250409_152135                        0.516968   0.726751  0.518918                0.5       0.514539  0.26475
XGBoost_3_AutoML_2_20250409_152135                    0.502451   0.893016  0.498844                0.5       0.561485  0.315265
XGBoost_1_AutoML_2_20250409_152135                    0.494532   0.847524  0.54791                 0.5       0.555468  0.308545
XGBoost_grid_1_AutoML_2_20250409_152135_model_2       0.486991   0.811853  0.492215                0.470023  0.543988  0.295923
DeepLearning_grid_2_AutoML_2_20250409_152135_model_1  0.483974   1.3188    0.466643                0.5       0.603914  0.364712
GBM_1_AutoML_2_20250409_152135                        0.48322    0.729637  0.481765                0.5       0.51663   0.266906
GBM_5_AutoML_2_20250409_152135                        0.478695   0.782243  0.491722                0.5       0.535926  0.287216
GBM_grid_1_AutoML_2_20250409_152135_model_2           0.467383   0.746436  0.482668                0.490196  0.523668  0.274228
XGBoost_grid_1_AutoML_2_20250409_152135_model_3       0.465875   0.950725  0.467881                0.490196  0.575634  0.331354
XGBoost_grid_1_AutoML_2_20250409_152135_model_1       0.463989   0.917712  0.465734                0.5       0.567556  0.32212
GBM_4_AutoML_2_20250409_152135                        0.463612   0.799223  0.464516                0.460407  0.542634  0.294452
GBM_3_AutoML_2_20250409_152135                        0.462104   0.803066  0.462236                0.5       0.542984  0.294832
DeepLearning_1_AutoML_2_20250409_152135               0.460219   0.884179  0.475068                0.5       0.56606   0.320424
GBM_2_AutoML_2_20250409_152135                        0.453808   0.804537  0.490487                0.5       0.545743  0.297836
XRT_1_AutoML_2_20250409_152135                        0.445701   0.753462  0.497824                0.5       0.527128  0.277864
DeepLearning_grid_1_AutoML_2_20250409_152135_model_1  0.437217   1.6811    0.460449                0.5       0.647546  0.419316
GLM_1_AutoML_2_20250409_152135                        0.434201   0.697165  0.460213                0.5       0.501997  0.252001
GBM_grid_1_AutoML_2_20250409_152135_model_1           0.432692   0.837016  0.44726                 0.5       0.5559    0.309025
DeepLearning_grid_3_AutoML_2_20250409_152135_model_1  0.428544   0.946621  0.449341                0.5       0.57934   0.335635
[20 rows x 7 columns]

In [22]:
lb = h2o.automl.get_leaderboard(aml, extra_columns = "ALL")
lb

model_id                                                   auc    logloss     aucpr    mean_per_class_error      rmse       mse    training_time_ms    predict_time_per_row_ms  algo
----------------------------------------------------  --------  ---------  --------  ----------------------  --------  --------  ------------------  -------------------------  ------------
XGBoost_2_AutoML_2_20250409_152135                    0.521682   0.868195  0.519441                0.490196  0.55289   0.305688                2467                   0.275334  XGBoost
DRF_1_AutoML_2_20250409_152135                        0.516968   0.726751  0.518918                0.5       0.514539  0.26475                 3142                   0.166365  DRF
XGBoost_3_AutoML_2_20250409_152135                    0.502451   0.893016  0.498844                0.5       0.561485  0.315265                3038                   0.202713  XGBoost
XGBoost_1_AutoML_2_20250409_152135                    0.494532   0.847524  0.54791                 0.5       0.555468  0.308545                2641                   0.203214  XGBoost
XGBoost_grid_1_AutoML_2_20250409_152135_model_2       0.486991   0.811853  0.492215                0.470023  0.543988  0.295923                6373                   0.162094  XGBoost
DeepLearning_grid_2_AutoML_2_20250409_152135_model_1  0.483974   1.3188    0.466643                0.5       0.603914  0.364712               33017                   0.198407  DeepLearning
GBM_1_AutoML_2_20250409_152135                        0.48322    0.729637  0.481765                0.5       0.51663   0.266906                3467                   0.126336  GBM
GBM_5_AutoML_2_20250409_152135                        0.478695   0.782243  0.491722                0.5       0.535926  0.287216                1649                   0.113597  GBM
GBM_grid_1_AutoML_2_20250409_152135_model_2           0.467383   0.746436  0.482668                0.490196  0.523668  0.274228                1230                   0.10611   GBM
XGBoost_grid_1_AutoML_2_20250409_152135_model_3       0.465875   0.950725  0.467881                0.490196  0.575634  0.331354                2592                   0.142199  XGBoost
[20 rows x 10 columns]

In [23]:
# Get the best model using the metric
m = aml.leader
print(m)

Model Details
H2OXGBoostEstimator : XGBoost
Model Key: XGBoost_2_AutoML_2_20250409_152135


Model Summary: 
    number_of_trees
--  -----------------
    30

ModelMetricsBinomial: xgboost
** Reported on train data. **

MSE: 0.04856159627892655
RMSE: 0.22036695822860228
LogLoss: 0.21811686278860418
Mean Per-Class Error: 0.0168651023003121
AUC: 0.9983354525488383
AUCPR: 0.9983430345133928
Gini: 0.9966709050976765

Confusion Matrix (Act/Pred) for max f1 @ threshold = 0.4844781955083211
       0    1    Error    Rate
-----  ---  ---  -------  ------------
0      402  8    0.0195   (8.0/410.0)
1      6    416  0.0142   (6.0/422.0)
Total  408  424  0.0168   (14.0/832.0)

Maximum Metrics: Maximum metrics at their respective thresholds
metric                       threshold    value     idx
---------------------------  -----------  --------  -----
max f1                       0.484478     0.983452  201
max f2                       0.445234     0.989657  212
max f0point5                 0.55107

In [24]:
# this is equivalent to
m = aml.get_best_model()
print(m)

Model Details
H2OXGBoostEstimator : XGBoost
Model Key: XGBoost_2_AutoML_2_20250409_152135


Model Summary: 
    number_of_trees
--  -----------------
    30

ModelMetricsBinomial: xgboost
** Reported on train data. **

MSE: 0.04856159627892655
RMSE: 0.22036695822860228
LogLoss: 0.21811686278860418
Mean Per-Class Error: 0.0168651023003121
AUC: 0.9983354525488383
AUCPR: 0.9983430345133928
Gini: 0.9966709050976765

Confusion Matrix (Act/Pred) for max f1 @ threshold = 0.4844781955083211
       0    1    Error    Rate
-----  ---  ---  -------  ------------
0      402  8    0.0195   (8.0/410.0)
1      6    416  0.0142   (6.0/422.0)
Total  408  424  0.0168   (14.0/832.0)

Maximum Metrics: Maximum metrics at their respective thresholds
metric                       threshold    value     idx
---------------------------  -----------  --------  -----
max f1                       0.484478     0.983452  201
max f2                       0.445234     0.989657  212
max f0point5                 0.55107

In [25]:
# Get the best model using a non-default metric
m = aml.get_best_model(criterion="logloss")
print(m)

Model Details
H2OGeneralizedLinearEstimator : Generalized Linear Modeling
Model Key: GLM_1_AutoML_2_20250409_152135


GLM Model: summary
    family    link    regularization             lambda_search                                                              number_of_predictors_total    number_of_active_predictors    number_of_iterations    training_frame
--  --------  ------  -------------------------  -------------------------------------------------------------------------  ----------------------------  -----------------------------  ----------------------  -----------------------------------------------
    binomial  logit   Ridge ( lambda = 8.3944 )  nlambda = 30, lambda.max = 8.3944, lambda.min = 8.3944, lambda.1se = -1.0  128                           128                            2                       AutoML_2_20250409_152135_training_py_3_sid_8ad7

ModelMetricsBinomialGLM: glm
** Reported on train data. **

MSE: 0.24717480793730287
RMSE: 0.49716678080630333
LogLoss: 0.68

In [26]:
# Get training timing info
info = aml.training_info
print(info)

{'creation_epoch': '1744212096', 'start_epoch': '1744212096', 'start_XGBoost_def_2': '1744212096', 'start_GLM_def_1': '1744212099', 'start_GBM_def_5': '1744212100', 'start_XGBoost_def_1': '1744212104', 'start_DRF_def_1': '1744212106', 'start_GBM_def_2': '1744212110', 'start_GBM_def_3': '1744212112', 'start_GBM_def_4': '1744212113', 'start_XGBoost_def_3': '1744212118', 'start_DRF_XRT': '1744212121', 'start_GBM_def_1': '1744212123', 'start_DeepLearning_def_1': '1744212125', 'start_XGBoost_grid_1': '1744212126', 'start_GBM_grid_1': '1744212139', 'start_DeepLearning_grid_1': '1744212141', 'start_DeepLearning_grid_2': '1744212171', 'start_DeepLearning_grid_3': '1744212204', 'stop_epoch': '1744212242', 'duration_secs': '146'}


In [27]:
aml.leader.model_id

'XGBoost_2_AutoML_2_20250409_152135'

In [28]:
preds_leader = aml.leader.predict(h2o_test)
preds_leader

xgboost prediction progress: |███████████████████████████████████████████████████| (done) 100%


predict        p0         p1
---------  --------  ---------
        1  0.470249  0.529751
        1  0.26728   0.73272
        1  0.308075  0.691925
        1  0.820202  0.179798
        1  0.815303  0.184697
        1  0.855976  0.144024
        1  0.777378  0.222622
        1  0.932411  0.0675895
        1  0.383299  0.616701
        1  0.541873  0.458127
[107 rows x 3 columns]

In [30]:
print("\n TRAIN SET \n")
train_predictions = aml.leader.predict(h2o_train).as_data_frame()['p1'].to_list()


print("\n VALID SET \n")
valid_predictions = aml.leader.predict(h2o_valid).as_data_frame()['p1'].to_list()


print("\n TEST SET \n")
test_predictions = aml.leader.predict(h2o_test).as_data_frame()['p1'].to_list()



text_only_preds = {}
text_only_preds['train_predictions'] = train_predictions
text_only_preds['valid_predictions'] = valid_predictions
text_only_preds['test_predictions'] = test_predictions


 TRAIN SET 

xgboost prediction progress: |███████████████████████████████████████████████████| (done) 100%

 VALID SET 

xgboost prediction progress: |███████████████████████████████████████████████████| (done) 100%

 TEST SET 

xgboost prediction progress: |███████████████████████████████████████████████████| (done) 100%


In [33]:
y_col = 'RESULT DATE+1 open price' #'TARGET-2 REGRESSION NORMALIZED'
x_cols_to_use = ['RESULT DATE open price', 'SMA20', 'SMA50', 'RSI14',
                 'gdp_growth', 'inflation', 'NIFTY50_open', 'NIFTY50_close', 'NIFTY50_volume',
                 'Sales', 'Expenses', 'Operating Profit', 'OPM %', 'Other Income', 'Interest',
                 'Depreciation', 'Profit before tax', 'Tax %', 'Net Profit',
                 'EPS in Rs', 'Dividend Payout %', 'Equity Capital', 'Reserves',
                 'Borrowings', 'Other Liabilities', 'Total Liabilities',
                 'Fixed Assets', 'CWIP', 'Investments', 'Other Assets',
                 'Total Assets', 'Cash from Operating Activity',
                 'Cash from Investing Activity', 'Cash from Financing Activity',
                 'Net Cash Flow', 'Revenue', 'Financing Profit', 'Financing Margin %',
                 'Deposits', 'Borrowing'] + ['text_probab']

train['text_probab'] = text_only_preds['train_predictions']
valid['text_probab'] = text_only_preds['valid_predictions']
test['text_probab'] = text_only_preds['test_predictions']



h2o_train = h2o.H2OFrame(train[x_cols_to_use])  # Convert train DataFrame to H2OFrame
h2o_valid = h2o.H2OFrame(valid[x_cols_to_use])  # Convert valid DataFrame to H2OFrame
h2o_test = h2o.H2OFrame(test[x_cols_to_use])  # Convert test DataFrame to H2OFrame

h2o_train[y_col] = h2o.H2OFrame(train[y_col].to_list())  # Convert Pandas Series to H2OFrame before assigning
h2o_valid[y_col] = h2o.H2OFrame(valid[y_col].to_list())  # Convert Pandas Series to H2OFrame before assigning
h2o_test[y_col] = h2o.H2OFrame(test[y_col].to_list())  # Convert Pandas Series to H2OFrame before assigning

aml = H2OAutoML(max_models=20, seed=1,nfolds = 0)
aml.train(x=x_cols_to_use, y=y_col, training_frame=h2o_train,validation_frame=h2o_valid)

# View the AutoML Leaderboard
lb = aml.leaderboard
lb.head(rows=lb.nrows)

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
AutoML progress: |███████████████████████████████████████████████████████████████| (done) 100%


model_id                                                  rmse               mse        mae      rmsle    mean_residual_deviance
----------------------------------------------------  --------  ----------------  ---------  ---------  ------------------------
DeepLearning_grid_1_AutoML_3_20250409_153059_model_1   115.115   13251.4            78.0504  0.198571            13251.4
DeepLearning_grid_2_AutoML_3_20250409_153059_model_1   219.796   48310.4           135.763   0.274313            48310.4
DeepLearning_grid_3_AutoML_3_20250409_153059_model_1   283.643   80453.3           150.574   0.268955            80453.3
DeepLearning_1_AutoML_3_20250409_153059                327.661  107362             163.088   0.31191            107362
GBM_5_AutoML_3_20250409_153059                         353.027  124628             121.656   0.058028           124628
XGBoost_grid_1_AutoML_3_20250409_153059_model_2        359.132  128976             129.895   0.0806582          128976
GBM_grid_1_AutoML_3_20250409_153059_model_2            364.131  132591             113.84    0.0775484          132591
XGBoost_3_AutoML_3_20250409_153059                     365.803  133812             133.642   0.0807689          133812
XGBoost_2_AutoML_3_20250409_153059                     369.732  136702             132.975   0.0898605          136702
XGBoost_grid_1_AutoML_3_20250409_153059_model_3        372.733  138930             120.947   0.0713517          138930
GBM_2_AutoML_3_20250409_153059                         393.985  155224             123.257   0.0878179          155224
GBM_3_AutoML_3_20250409_153059                         397.278  157830             125.504   0.0984018          157830
GBM_4_AutoML_3_20250409_153059                         397.613  158096             119.102   0.0840173          158096
XGBoost_grid_1_AutoML_3_20250409_153059_model_1        411.003  168924             165.744   0.106208           168924
XGBoost_1_AutoML_3_20250409_153059                     421.675  177810             156.022   0.0850261          177810
GBM_grid_1_AutoML_3_20250409_153059_model_1            431.237  185966             184.649   0.240062           185966
XRT_1_AutoML_3_20250409_153059                         451.33   203698             170.92    0.138523           203698
DRF_1_AutoML_3_20250409_153059                         454.358  206441             163.565   0.0777229          206441
GBM_1_AutoML_3_20250409_153059                        1159.54        1.34453e+06   471.462   0.304123                1.34453e+06
GLM_1_AutoML_3_20250409_153059                        2474.66        6.12395e+06  1514.8     1.18928                 6.12395e+06
[20 rows x 6 columns]

In [34]:
lb = h2o.automl.get_leaderboard(aml, extra_columns = "ALL")
lb

model_id                                                 rmse       mse       mae      rmsle    mean_residual_deviance    training_time_ms    predict_time_per_row_ms  algo
----------------------------------------------------  -------  --------  --------  ---------  ------------------------  ------------------  -------------------------  ------------
DeepLearning_grid_1_AutoML_3_20250409_153059_model_1  115.115   13251.4   78.0504  0.198571                    13251.4               81106                   0.062635  DeepLearning
DeepLearning_grid_2_AutoML_3_20250409_153059_model_1  219.796   48310.4  135.763   0.274313                    48310.4               58250                   0.09149   DeepLearning
DeepLearning_grid_3_AutoML_3_20250409_153059_model_1  283.643   80453.3  150.574   0.268955                    80453.3               40590                   0.173145  DeepLearning
DeepLearning_1_AutoML_3_20250409_153059               327.661  107362    163.088   0.31191                    107362                   483                   0.025744  DeepLearning
GBM_5_AutoML_3_20250409_153059                        353.027  124628    121.656   0.058028                   124628                  1445                   0.047336  GBM
XGBoost_grid_1_AutoML_3_20250409_153059_model_2       359.132  128976    129.895   0.0806582                  128976                  4941                   0.084215  XGBoost
GBM_grid_1_AutoML_3_20250409_153059_model_2           364.131  132591    113.84    0.0775484                  132591                  1040                   0.045228  GBM
XGBoost_3_AutoML_3_20250409_153059                    365.803  133812    133.642   0.0807689                  133812                   610                   0.032342  XGBoost
XGBoost_2_AutoML_3_20250409_153059                    369.732  136702    132.975   0.0898605                  136702                  2056                   0.040969  XGBoost
XGBoost_grid_1_AutoML_3_20250409_153059_model_3       372.733  138930    120.947   0.0713517                  138930                  1874                   0.032302  XGBoost
[20 rows x 9 columns]

In [35]:
# Get the best model using the metric
m = aml.leader
print(m)

Model Details
H2ODeepLearningEstimator : Deep Learning
Model Key: DeepLearning_grid_1_AutoML_3_20250409_153059_model_1


Status of Neuron Layers: predicting RESULT DATE+1 open price, regression, gaussian distribution, Quadratic loss, 28,201 weights/biases, 346.8 KB, 858,931 training samples, mini-batch size 1
    layer    units    type              dropout    l1    l2    mean_rate              rate_rms               momentum    mean_weight             weight_rms           mean_bias             bias_rms
--  -------  -------  ----------------  ---------  ----  ----  ---------------------  ---------------------  ----------  ----------------------  -------------------  --------------------  -----------------------
    1        280      Input             15.0
    2        100      RectifierDropout  10.0       0.0   0.0   0.04534329561915365    0.1347193717956543     0.0         -0.0048023015300245305  0.07585853338241577  0.06739497309629429   0.1536393165588379
    3        1        Linear

In [36]:
# this is equivalent to
m = aml.get_best_model()
print(m)

Model Details
H2ODeepLearningEstimator : Deep Learning
Model Key: DeepLearning_grid_1_AutoML_3_20250409_153059_model_1


Status of Neuron Layers: predicting RESULT DATE+1 open price, regression, gaussian distribution, Quadratic loss, 28,201 weights/biases, 346.8 KB, 858,931 training samples, mini-batch size 1
    layer    units    type              dropout    l1    l2    mean_rate              rate_rms               momentum    mean_weight             weight_rms           mean_bias             bias_rms
--  -------  -------  ----------------  ---------  ----  ----  ---------------------  ---------------------  ----------  ----------------------  -------------------  --------------------  -----------------------
    1        280      Input             15.0
    2        100      RectifierDropout  10.0       0.0   0.0   0.04534329561915365    0.1347193717956543     0.0         -0.0048023015300245305  0.07585853338241577  0.06739497309629429   0.1536393165588379
    3        1        Linear

In [37]:
# Get the best model using a non-default metric
m = aml.get_best_model(criterion="RMSE")
print(m)

Model Details
H2ODeepLearningEstimator : Deep Learning
Model Key: DeepLearning_grid_1_AutoML_3_20250409_153059_model_1


Status of Neuron Layers: predicting RESULT DATE+1 open price, regression, gaussian distribution, Quadratic loss, 28,201 weights/biases, 346.8 KB, 858,931 training samples, mini-batch size 1
    layer    units    type              dropout    l1    l2    mean_rate              rate_rms               momentum    mean_weight             weight_rms           mean_bias             bias_rms
--  -------  -------  ----------------  ---------  ----  ----  ---------------------  ---------------------  ----------  ----------------------  -------------------  --------------------  -----------------------
    1        280      Input             15.0
    2        100      RectifierDropout  10.0       0.0   0.0   0.04534329561915365    0.1347193717956543     0.0         -0.0048023015300245305  0.07585853338241577  0.06739497309629429   0.1536393165588379
    3        1        Linear

In [38]:
# Get training timing info
info = aml.training_info
print(info)

{'creation_epoch': '1744212660', 'start_epoch': '1744212660', 'start_XGBoost_def_2': '1744212660', 'start_GLM_def_1': '1744212669', 'start_GBM_def_5': '1744212670', 'start_XGBoost_def_1': '1744212672', 'start_DRF_def_1': '1744212674', 'start_GBM_def_2': '1744212678', 'start_GBM_def_3': '1744212680', 'start_GBM_def_4': '1744212684', 'start_XGBoost_def_3': '1744212688', 'start_DRF_XRT': '1744212688', 'start_GBM_def_1': '1744212692', 'start_DeepLearning_def_1': '1744212693', 'start_XGBoost_grid_1': '1744212694', 'start_GBM_grid_1': '1744212703', 'start_DeepLearning_grid_1': '1744212705', 'start_DeepLearning_grid_2': '1744212787', 'start_DeepLearning_grid_3': '1744212845', 'stop_epoch': '1744212886', 'duration_secs': '226'}


In [39]:
aml.leader.model_id

'DeepLearning_grid_1_AutoML_3_20250409_153059_model_1'

In [40]:
preds_leader = aml.leader.predict(h2o_test)
preds_leader

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%


predict
---------
 111.347
 949.212
1912.91
  79.4909
 121.781
2905.96
4425.99
 637.457
 684.523
 991.548
[107 rows x 1 column]

In [41]:
print("\n TRAIN SET \n")
train_predictions = aml.leader.predict(h2o_train).as_data_frame()['predict'].to_list()
print(calculate_regression_metrics(train[y_col], train_predictions))

print("\n VALID SET \n")
valid_predictions = aml.leader.predict(h2o_valid).as_data_frame()['predict'].to_list()
print(calculate_regression_metrics(valid[y_col], valid_predictions))

print("\n TEST SET \n")
test_predictions = aml.leader.predict(h2o_test).as_data_frame()['predict'].to_list()
print(calculate_regression_metrics(test[y_col],test_predictions))


 TRAIN SET 

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%
{'MAE': 72.6657340887975, 'RMSE': np.float64(95.77964918899451), 'MAPE': 0.27260300292523304}

 VALID SET 

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%
{'MAE': 78.05043850896263, 'RMSE': np.float64(115.11468693949165), 'MAPE': 0.12153298746353784}

 TEST SET 

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%
{'MAE': 125.20351368229714, 'RMSE': np.float64(216.63874679442355), 'MAPE': 0.3489434709529733}


# Using Numeric, Text Data Classifier Probabilities, and Image Data Classifier Probabilities

In [43]:
for col in final_with_funda.columns:
  if 'text_embeddings' in col:
    print(col)
    del final_with_funda[col]

# all_embeddings_128 = pickle.load(open(path + 'getting_all_texts_together_embeddings_dim128_CPU.pkl', 'rb'))
# final_with_funda['text_embeddings'] = all_embeddings_128

# for i in range(128):
#   final_with_funda['text_embeddings_' + str(i)] = final_with_funda['text_embeddings'].apply(lambda x : x[i])

# text_features = ['text_embeddings_' + str(i) for i in range(128)]

text_embeddings
text_embeddings_0
text_embeddings_1
text_embeddings_2
text_embeddings_3
text_embeddings_4
text_embeddings_5
text_embeddings_6
text_embeddings_7
text_embeddings_8
text_embeddings_9
text_embeddings_10
text_embeddings_11
text_embeddings_12
text_embeddings_13
text_embeddings_14
text_embeddings_15
text_embeddings_16
text_embeddings_17
text_embeddings_18
text_embeddings_19
text_embeddings_20
text_embeddings_21
text_embeddings_22
text_embeddings_23
text_embeddings_24
text_embeddings_25
text_embeddings_26
text_embeddings_27
text_embeddings_28
text_embeddings_29
text_embeddings_30
text_embeddings_31
text_embeddings_32
text_embeddings_33
text_embeddings_34
text_embeddings_35
text_embeddings_36
text_embeddings_37
text_embeddings_38
text_embeddings_39
text_embeddings_40
text_embeddings_41
text_embeddings_42
text_embeddings_43
text_embeddings_44
text_embeddings_45
text_embeddings_46
text_embeddings_47
text_embeddings_48
text_embeddings_49
text_embeddings_50
text_embeddings_51
text_e

In [44]:
img_emd_df = pd.read_csv(path + "image_embedding_mean_pooled_128_dim_CPU_df.csv")
final_with_funda = pd.concat([final_with_funda, img_emd_df] , axis = 1)

In [48]:
image_features = ["image_embedding_" + str(i) for i in range(128)]

train = final_with_funda[final_with_funda['split'] == 'train']
valid = final_with_funda[final_with_funda['split'] == 'validation']
test = final_with_funda[final_with_funda['split'] == 'test']

x_cols_to_use =  image_features

In [49]:
y_col =  'classification' #'RESULT DATE+1 open price'#'TARGET-2 REGRESSION NORMALIZED'

h2o_train = h2o.H2OFrame(train[x_cols_to_use])  # Convert train DataFrame to H2OFrame
h2o_valid = h2o.H2OFrame(valid[x_cols_to_use])  # Convert valid DataFrame to H2OFrame
h2o_test = h2o.H2OFrame(test[x_cols_to_use])  # Convert test DataFrame to H2OFrame

h2o_train[y_col] = h2o.H2OFrame(train[y_col].to_list()).asfactor()  # Convert Pandas Series to H2OFrame before assigning
h2o_valid[y_col] = h2o.H2OFrame(valid[y_col].to_list()).asfactor()  # Convert Pandas Series to H2OFrame before assigning
h2o_test[y_col] = h2o.H2OFrame(test[y_col].to_list()).asfactor()  # Convert Pandas Series to H2OFrame before assigning

aml = H2OAutoML(max_models=20, seed=1,nfolds = 0)
aml.train(x=x_cols_to_use, y=y_col, training_frame=h2o_train,validation_frame=h2o_valid)

# View the AutoML Leaderboard
lb = aml.leaderboard
lb.head(rows=lb.nrows)

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
AutoML progress: |███████████████████████████████████████████████████████████████| (done) 100%


model_id                                                   auc    logloss     aucpr    mean_per_class_error      rmse       mse
----------------------------------------------------  --------  ---------  --------  ----------------------  --------  --------
XRT_1_AutoML_4_20250409_154354                        0.503017   0.733152  0.484082                0.480392  0.516668  0.266945
XGBoost_grid_1_AutoML_4_20250409_154354_model_1       0.488499   0.847333  0.503155                0.5       0.548085  0.300397
GBM_grid_1_AutoML_4_20250409_154354_model_2           0.487745   0.724781  0.476677                0.470588  0.514349  0.264555
GLM_1_AutoML_4_20250409_154354                        0.486991   0.692994  0.534541                0.4704    0.499927  0.249927
GBM_2_AutoML_4_20250409_154354                        0.481335   0.792884  0.465885                0.490196  0.537859  0.289292
GBM_4_AutoML_4_20250409_154354                        0.479072   0.766912  0.484253                0.480392  0.530249  0.281163
XGBoost_3_AutoML_4_20250409_154354                    0.477941   0.868045  0.477292                0.5       0.557476  0.310779
DeepLearning_grid_2_AutoML_4_20250409_154354_model_1  0.473039   1.05933   0.456692                0.450603  0.596275  0.355543
DeepLearning_1_AutoML_4_20250409_154354               0.472662   0.857147  0.486409                0.5       0.550378  0.302916
DeepLearning_grid_3_AutoML_4_20250409_154354_model_1  0.468514   0.844478  0.459279                0.5       0.549941  0.302435
DRF_1_AutoML_4_20250409_154354                        0.467195   0.760494  0.452942                0.5       0.527926  0.278706
DeepLearning_grid_1_AutoML_4_20250409_154354_model_1  0.462858   1.32825   0.463777                0.5       0.60405   0.364876
XGBoost_grid_1_AutoML_4_20250409_154354_model_3       0.458333   0.917929  0.45348                 0.5       0.568323  0.322991
GBM_1_AutoML_4_20250409_154354                        0.45494    0.719961  0.459342                0.470211  0.512716  0.262878
GBM_5_AutoML_4_20250409_154354                        0.453808   0.776823  0.455488                0.460219  0.53518   0.286418
XGBoost_grid_1_AutoML_4_20250409_154354_model_2       0.4523     0.860165  0.447011                0.5       0.559062  0.31255
GBM_grid_1_AutoML_4_20250409_154354_model_1           0.439103   0.796162  0.464251                0.490008  0.543544  0.29544
XGBoost_2_AutoML_4_20250409_154354                    0.435332   1.03246   0.449842                0.5       0.594755  0.353734
XGBoost_1_AutoML_4_20250409_154354                    0.429299   0.86822   0.437805                0.5       0.563479  0.317509
GBM_3_AutoML_4_20250409_154354                        0.40856    0.819399  0.431929                0.480392  0.552144  0.304863
[20 rows x 7 columns]

In [50]:
lb = h2o.automl.get_leaderboard(aml, extra_columns = "ALL")
lb

model_id                                                   auc    logloss     aucpr    mean_per_class_error      rmse       mse    training_time_ms    predict_time_per_row_ms  algo
----------------------------------------------------  --------  ---------  --------  ----------------------  --------  --------  ------------------  -------------------------  ------------
XRT_1_AutoML_4_20250409_154354                        0.503017   0.733152  0.484082                0.480392  0.516668  0.266945                1101                   0.129188  DRF
XGBoost_grid_1_AutoML_4_20250409_154354_model_1       0.488499   0.847333  0.503155                0.5       0.548085  0.300397                1456                   0.102439  XGBoost
GBM_grid_1_AutoML_4_20250409_154354_model_2           0.487745   0.724781  0.476677                0.470588  0.514349  0.264555                1472                   0.096619  GBM
GLM_1_AutoML_4_20250409_154354                        0.486991   0.692994  0.534541                0.4704    0.499927  0.249927                 573                   0.145861  GLM
GBM_2_AutoML_4_20250409_154354                        0.481335   0.792884  0.465885                0.490196  0.537859  0.289292                1917                   0.13284   GBM
GBM_4_AutoML_4_20250409_154354                        0.479072   0.766912  0.484253                0.480392  0.530249  0.281163                1843                   0.101481  GBM
XGBoost_3_AutoML_4_20250409_154354                    0.477941   0.868045  0.477292                0.5       0.557476  0.310779                 999                   0.090673  XGBoost
DeepLearning_grid_2_AutoML_4_20250409_154354_model_1  0.473039   1.05933   0.456692                0.450603  0.596275  0.355543               32263                   0.134248  DeepLearning
DeepLearning_1_AutoML_4_20250409_154354               0.472662   0.857147  0.486409                0.5       0.550378  0.302916                 353                   0.0919    DeepLearning
DeepLearning_grid_3_AutoML_4_20250409_154354_model_1  0.468514   0.844478  0.459279                0.5       0.549941  0.302435               33586                   0.160156  DeepLearning
[20 rows x 10 columns]

In [51]:
# Get the best model using the metric
m = aml.leader
print(m)
# this is equivalent to
m = aml.get_best_model()
print(m)
# Get the best model using a non-default metric
m = aml.get_best_model(criterion="logloss")
print(m)
# Get training timing info
info = aml.training_info
print(info)


Could not find exact threshold 0.0; using closest threshold found 0.0.
Model Details
H2ORandomForestEstimator : Distributed Random Forest
Model Key: XRT_1_AutoML_4_20250409_154354


Model Summary: 
    number_of_trees    number_of_internal_trees    model_size_in_bytes    min_depth    max_depth    mean_depth    min_leaves    max_leaves    mean_leaves
--  -----------------  --------------------------  ---------------------  -----------  -----------  ------------  ------------  ------------  -------------
    40                 40                          54873                  13           20           16.5          94            115           104.475

ModelMetricsBinomial: drf
** Reported on train data. **

MSE: 0.27357332063544987
RMSE: 0.5230423698281526
LogLoss: 0.8737924656542455
Mean Per-Class Error: 0.5
AUC: 0.5218963125650214
AUCPR: 0.5305415130974961
Gini: 0.043792625130042895

Confusion Matrix (Act/Pred) for max f1 @ threshold = 0.0
       0    1    Error    Rate
-----  ---  --

In [52]:
aml.leader.model_id

'XRT_1_AutoML_4_20250409_154354'

In [53]:
preds_leader = aml.leader.predict(h2o_test)
preds_leader


drf prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict        p0        p1
---------  --------  --------
        1  0.575     0.425
        1  0.202551  0.797449
        1  0.470319  0.529681
        1  0.35      0.65
        1  0.470319  0.529681
        1  0.5875    0.4125
        1  0.425     0.575
        1  0.7       0.3
        1  0.470319  0.529681
        1  0.55      0.45
[107 rows x 3 columns]

In [54]:
print("\n TRAIN SET \n")
train_predictions = aml.leader.predict(h2o_train).as_data_frame()['p1'].to_list()


print("\n VALID SET \n")
valid_predictions = aml.leader.predict(h2o_valid).as_data_frame()['p1'].to_list()

print("\n TEST SET \n")
test_predictions = aml.leader.predict(h2o_test).as_data_frame()['p1'].to_list()

image_only_preds = {}
image_only_preds['train_predictions'] = train_predictions
image_only_preds['valid_predictions'] = valid_predictions
image_only_preds['test_predictions'] = test_predictions


 TRAIN SET 

drf prediction progress: |███████████████████████████████████████████████████████| (done) 100%

 VALID SET 

drf prediction progress: |███████████████████████████████████████████████████████| (done) 100%

 TEST SET 

drf prediction progress: |███████████████████████████████████████████████████████| (done) 100%


In [71]:
y_col = 'RESULT DATE+1 open price' #'TARGET-2 REGRESSION NORMALIZED'
x_cols_to_use = ['RESULT DATE open price', 'SMA20', 'SMA50', 'RSI14',
                 'gdp_growth', 'inflation', 'NIFTY50_open', 'NIFTY50_close', 'NIFTY50_volume',
                 'Sales', 'Expenses', 'Operating Profit', 'OPM %', 'Other Income', 'Interest',
                 'Depreciation', 'Profit before tax', 'Tax %', 'Net Profit',
                 'EPS in Rs', 'Dividend Payout %', 'Equity Capital', 'Reserves',
                 'Borrowings', 'Other Liabilities', 'Total Liabilities',
                 'Fixed Assets', 'CWIP', 'Investments', 'Other Assets',
                 'Total Assets', 'Cash from Operating Activity',
                 'Cash from Investing Activity', 'Cash from Financing Activity',
                 'Net Cash Flow', 'Revenue', 'Financing Profit', 'Financing Margin %',
                 'Deposits', 'Borrowing'] + ['text_probab'] + ['image_probab']

train['text_probab'] = text_only_preds['train_predictions']
valid['text_probab'] = text_only_preds['valid_predictions']
test['text_probab'] = text_only_preds['test_predictions']

train['image_probab'] = image_only_preds['train_predictions']
valid['image_probab'] = image_only_preds['valid_predictions']
test['image_probab'] = image_only_preds['test_predictions']

h2o_train = h2o.H2OFrame(train[x_cols_to_use])  # Convert train DataFrame to H2OFrame
h2o_valid = h2o.H2OFrame(valid[x_cols_to_use])  # Convert valid DataFrame to H2OFrame
h2o_test = h2o.H2OFrame(test[x_cols_to_use])  # Convert test DataFrame to H2OFrame

h2o_train[y_col] = h2o.H2OFrame(train[y_col].to_list())  # Convert Pandas Series to H2OFrame before assigning
h2o_valid[y_col] = h2o.H2OFrame(valid[y_col].to_list())  # Convert Pandas Series to H2OFrame before assigning
h2o_test[y_col] = h2o.H2OFrame(test[y_col].to_list())  # Convert Pandas Series to H2OFrame before assigning

aml = H2OAutoML(max_models=100, seed=1,nfolds = 0)
aml.train(x=x_cols_to_use, y=y_col, training_frame=h2o_train,validation_frame=h2o_valid)

# View the AutoML Leaderboard
lb = aml.leaderboard
lb.head(rows=lb.nrows)

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
AutoML progress: |███████████████████████████████████████████████████████████████| (done) 100%


model_id                                                   rmse               mse        mae        rmsle    mean_residual_deviance
-----------------------------------------------------  --------  ----------------  ---------  -----------  ------------------------
DeepLearning_grid_1_AutoML_7_20250409_160125_model_9    100.024   10004.8            64.5561    0.266664            10004.8
DeepLearning_grid_1_AutoML_7_20250409_160125_model_1    134.704   18145.1            90.0874    0.188638            18145.1
DeepLearning_grid_1_AutoML_7_20250409_160125_model_4    135.642   18398.7           100.929     0.194114            18398.7
DeepLearning_grid_1_AutoML_7_20250409_160125_model_10   149.507   22352.2            89.8572  nan                   22352.2
DeepLearning_grid_1_AutoML_7_20250409_160125_model_5    164.876   27184.1           113.692     0.253921            27184.1
DeepLearning_grid_2_AutoML_7_20250409_160125_model_4    168.761   28480.3           136.099     0.283903            28480.3
DeepLearning_grid_1_AutoML_7_20250409_160125_model_2    188.361   35479.9           138.995   nan                   35479.9
DeepLearning_grid_2_AutoML_7_20250409_160125_model_10   193.53    37453.7           139.606   nan                   37453.7
DeepLearning_grid_3_AutoML_7_20250409_160125_model_4    203.619   41460.6           118.388     0.214535            41460.6
DeepLearning_grid_3_AutoML_7_20250409_160125_model_7    205.314   42154             121.346     0.22253             42154
DeepLearning_grid_3_AutoML_7_20250409_160125_model_1    207.528   43067.9           116.164     0.314633            43067.9
DeepLearning_grid_3_AutoML_7_20250409_160125_model_10   215.478   46430.7           114.794     0.193609            46430.7
DeepLearning_grid_1_AutoML_7_20250409_160125_model_7    217.389   47258             147.873   nan                   47258
DeepLearning_grid_1_AutoML_7_20250409_160125_model_6    221.629   49119.5           144.504     0.25002             49119.5
DeepLearning_grid_2_AutoML_7_20250409_160125_model_1    235.728   55567.5           186.976     0.349211            55567.5
DeepLearning_grid_2_AutoML_7_20250409_160125_model_7    248.525   61764.6           181.495   nan                   61764.6
DeepLearning_grid_1_AutoML_7_20250409_160125_model_3    257.242   66173.4           169.275   nan                   66173.4
DeepLearning_grid_1_AutoML_7_20250409_160125_model_11   257.672   66395.1           161.105   nan                   66395.1
DeepLearning_grid_3_AutoML_7_20250409_160125_model_8    275.723   76023             186.465   nan                   76023
XGBoost_grid_1_AutoML_7_20250409_160125_model_8         322.575  104055             118.816     0.061503           104055
XGBoost_grid_1_AutoML_7_20250409_160125_model_13        323.824  104862             122.203     0.0652133          104862
XGBoost_grid_1_AutoML_7_20250409_160125_model_23        334.453  111859             119.161     0.0863272          111859
XGBoost_grid_1_AutoML_7_20250409_160125_model_31        343.315  117865             126.802     0.102759           117865
DeepLearning_1_AutoML_7_20250409_160125                 345.776  119561             180.892   nan                  119561
DeepLearning_grid_2_AutoML_7_20250409_160125_model_6    350.948  123165             253.962     0.571391           123165
DeepLearning_grid_1_AutoML_7_20250409_160125_model_8    352.587  124317             263.534   nan                  124317
XGBoost_grid_1_AutoML_7_20250409_160125_model_27        352.811  124476             145.251     0.0781429          124476
XGBoost_grid_1_AutoML_7_20250409_160125_model_25        354.925  125972             126.807     0.098505           125972
XGBoost_3_AutoML_7_20250409_160125                      356.462  127065             133.239     0.0937253          127065
XGBoost_grid_1_AutoML_7_20250409_160125_model_24        361.243  130496             149.89      0.0855626          130496
DeepLearning_grid_2_AutoML_7_20250409_160125

In [72]:
lb = h2o.automl.get_leaderboard(aml, extra_columns = "ALL")
lb

model_id                                                  rmse      mse       mae       rmsle    mean_residual_deviance    training_time_ms    predict_time_per_row_ms  algo
-----------------------------------------------------  -------  -------  --------  ----------  ------------------------  ------------------  -------------------------  ------------
DeepLearning_grid_1_AutoML_7_20250409_160125_model_9   100.024  10004.8   64.5561    0.266664                   10004.8               40893                   0.051003  DeepLearning
DeepLearning_grid_1_AutoML_7_20250409_160125_model_1   134.704  18145.1   90.0874    0.188638                   18145.1               43225                   0.067006  DeepLearning
DeepLearning_grid_1_AutoML_7_20250409_160125_model_4   135.642  18398.7  100.929     0.194114                   18398.7              102919                   0.063598  DeepLearning
DeepLearning_grid_1_AutoML_7_20250409_160125_model_10  149.507  22352.2   89.8572  nan                          22352.2               40231                   0.054317  DeepLearning
DeepLearning_grid_1_AutoML_7_20250409_160125_model_5   164.876  27184.1  113.692     0.253921                   27184.1               31895                   0.075369  DeepLearning
DeepLearning_grid_2_AutoML_7_20250409_160125_model_4   168.761  28480.3  136.099     0.283903                   28480.3               59139                   0.085656  DeepLearning
DeepLearning_grid_1_AutoML_7_20250409_160125_model_2   188.361  35479.9  138.995   nan                          35479.9               46488                   0.038126  DeepLearning
DeepLearning_grid_2_AutoML_7_20250409_160125_model_10  193.53   37453.7  139.606   nan                          37453.7               36671                   0.066524  DeepLearning
DeepLearning_grid_3_AutoML_7_20250409_160125_model_4   203.619  41460.6  118.388     0.214535                   41460.6               62840                   0.079879  DeepLearning
DeepLearning_grid_3_AutoML_7_20250409_160125_model_7   205.314  42154    121.346     0.22253                    42154                106315                   0.082181  DeepLearning
[100 rows x 9 columns]

In [73]:
# Get the best model using the metric
m = aml.leader
print(m)

Model Details
H2ODeepLearningEstimator : Deep Learning
Model Key: DeepLearning_grid_1_AutoML_7_20250409_160125_model_9


Status of Neuron Layers: predicting RESULT DATE+1 open price, regression, gaussian distribution, Quadratic loss, 5,661 weights/biases, 81.9 KB, 2,254,720 training samples, mini-batch size 1
    layer    units    type              dropout    l1    l2    mean_rate             rate_rms              momentum    mean_weight            weight_rms           mean_bias            bias_rms
--  -------  -------  ----------------  ---------  ----  ----  --------------------  --------------------  ----------  ---------------------  -------------------  -------------------  -----------------------
    1        281      Input             0.0
    2        20       RectifierDropout  10.0       0.0   0.0   0.1224201583713347    0.24743318557739258   0.0         -0.003040129768628973  0.10864239931106567  0.31249810220787977  0.49442625045776367
    3        1        Linear            

In [74]:
# Get training timing info
info = aml.training_info
print(info)

{'creation_epoch': '1744214486', 'start_epoch': '1744214486', 'start_XGBoost_def_2': '1744214486', 'start_GLM_def_1': '1744214488', 'start_GBM_def_5': '1744214488', 'start_XGBoost_def_1': '1744214488', 'start_DRF_def_1': '1744214489', 'start_GBM_def_2': '1744214491', 'start_GBM_def_3': '1744214492', 'start_GBM_def_4': '1744214494', 'start_XGBoost_def_3': '1744214495', 'start_DRF_XRT': '1744214496', 'start_GBM_def_1': '1744214499', 'start_DeepLearning_def_1': '1744214501', 'start_XGBoost_grid_1': '1744214501', 'start_GBM_grid_1': '1744214574', 'start_DeepLearning_grid_1': '1744214600', 'start_DeepLearning_grid_2': '1744215129', 'start_DeepLearning_grid_3': '1744215596', 'stop_epoch': '1744216240', 'duration_secs': '1754'}


In [75]:
aml.leader.model_id

'DeepLearning_grid_1_AutoML_7_20250409_160125_model_9'

In [76]:
preds_leader = aml.leader.predict(h2o_test)
preds_leader

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%


predict
----------
   9.18649
1006.17
1854.82
  81.9125
  97.5076
2888.97
4506.62
 637.33
 617.228
1029.59
[107 rows x 1 column]

In [77]:
print("\n TRAIN SET \n")
train_predictions = aml.leader.predict(h2o_train).as_data_frame()['predict'].to_list()
print(calculate_regression_metrics(train[y_col], train_predictions))

print("\n VALID SET \n")
valid_predictions = aml.leader.predict(h2o_valid).as_data_frame()['predict'].to_list()
print(calculate_regression_metrics(valid[y_col], valid_predictions))

print("\n TEST SET \n")
test_predictions = aml.leader.predict(h2o_test).as_data_frame()['predict'].to_list()
print(calculate_regression_metrics(test[y_col],test_predictions))


 TRAIN SET 

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%
{'MAE': 39.35300733202008, 'RMSE': np.float64(66.21786015854784), 'MAPE': 0.14468676367502867}

 VALID SET 

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%
{'MAE': 64.55607585185871, 'RMSE': np.float64(100.02399540743662), 'MAPE': 0.07541354069196421}

 TEST SET 

deeplearning prediction progress: |██████████████████████████████████████████████| (done) 100%
{'MAE': 104.78748524053184, 'RMSE': np.float64(188.53744596018586), 'MAPE': 0.333730313262129}


In [82]:
best_model = aml.get_best_model()
model_path = h2o.save_model(model=best_model, path=path + "mimic_best_model", force=True)

/content/drive/MyDrive/datasets/Multimodal_EarningCallTranscripts_Analysis_India/mimic_best_model/DeepLearning_grid_1_AutoML_7_20250409_160125_model_9


In [ ]:
# To load the model, use the following commands
# !unzip Best_Performing_Model_on_MiMIC.zip
# loaded_model = h2o.load_model("DeepLearning_grid_1_AutoML_7_20250409_160125_model_9")